In [1]:
from transformers import AutoTokenizer

checkpoint = "google-t5/t5-small"
tokenizer = AutoTokenizer.from_pretrained(checkpoint)

In [2]:
prefix = "summarize: "


def preprocess_function(examples):
    inputs = [prefix + doc for doc in examples["text"]]
    model_inputs = tokenizer(inputs, max_length=1024, truncation=True)

    labels = tokenizer(text_target=examples["summary"], max_length=128, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

In [3]:
from transformers import DataCollatorForSeq2Seq

data_collator = DataCollatorForSeq2Seq(tokenizer=tokenizer, model=checkpoint)

2024-04-10 19:08:16.517364: I tensorflow/core/util/port.cc:111] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-04-10 19:08:16.557667: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-04-10 19:08:16.557712: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-04-10 19:08:16.557734: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-04-10 19:08:16.565003: I tensorflow/core/platform/cpu_feature_g

In [4]:
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    decoded_preds = tokenizer.batch_decode(predictions, skip_special_tokens=True)
    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)

    result = rouge.compute(predictions=decoded_preds, references=decoded_labels, use_stemmer=True)

    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in predictions]
    result["gen_len"] = np.mean(prediction_lens)

    return {k: round(v, 4) for k, v in result.items()}

In [5]:
import json

cleaned_test_data = []
# Opening JSON file
with open("cleaned_bill_sum_test_data.json") as json_file:
    cleaned_test_data = json.load(json_file)

In [6]:
from transformers import AutoModelForSeq2SeqLM, Seq2SeqTrainingArguments, Seq2SeqTrainer

model = AutoModelForSeq2SeqLM.from_pretrained(checkpoint)

In [7]:
from transformers import pipeline

summarizer = pipeline("summarization", model=model, tokenizer=tokenizer)

In [8]:
generated_summaries = []
for i in range(len(cleaned_test_data)):
    summary = summarizer(cleaned_test_data[i]['text'])
    generated_summaries.append({"generated" : summary[0]['summary_text'], "summary" : cleaned_test_data[i]['summary']})

Token indices sequence length is longer than the specified maximum sequence length for this model (548 > 512). Running this sequence through the model will result in indexing errors


In [9]:
generated_summaries[0]

{'generated': 'ACCEPT resolution 2023-01-25 Introduced in Senate Adopting Cryptocurrency in Congress as an Exchange of Payment for Transactions Resolution or the ACCEPT Resolution This resolution requires the Architect of the Capitol, the Secretary of the Senate, and the Chief Administrative Officer of the House of Representatives to encourage Capitol gift shops to accept cryptocurrency . this file contains bill summaries for federal legislation .',
 'summary': 'Adopting Cryptocurrency in Congress as an Exchange of Payment for Transactions Resolution or the ACCEPT Resolution This resolution requires the Architect of the Capitol, the Secretary of the Senate, and the Chief Administrative Officer of the House of Representatives to encourage Capitol gift shops to accept cryptocurrency and to enter into contracts with vendors that accept cryptocurrency to provide food service and vending machines in the Capitol.'}

In [10]:
generated_summaries[1]

{'generated': '2023-07-25 Introduced in Senate This concurrent resolution commends the bravery, courage, and resolve of the women and men of Iran . the resolution condemns (1) the brutal beating and death of Mahsa Amini; (2) the violent suppression by the Iranian regime of women and women participating in the current demonstrations .',
 'summary': 'This concurrent resolution commends the bravery, courage, and resolve of the women and men of Iran who are (1) participating in the current protests to defend their fundamental human rights, and (2) risking their safety to speak out against the human rights abuses committed by the Iranian regime. The resolution condemns (1) the brutal beating and death of Mahsa Amini; and (2) the violent suppression by the Iranian regime of women and men participating in the current demonstrations, including children, and calls for transparent accountability for all killings of protesters by Iranian security forces. Finally, the resolution encourages continu

In [11]:
generated_summaries[2]

{'generated': 'a concurrent resolution calls for honoring the 237th anniversary of the enactment of the Virginia Statute for Religious Freedom on religious freedom day, January 16, 2023 . the resolution affirms that religious freedom includes the right of individuals of any faith and individuals of no faith to live, work, associate, and worship .',
 'summary': 'This concurrent resolution calls for honoring the 237th anniversary of the enactment of the Virginia Statute for Religious Freedom on Religious Freedom Day, January 16, 2023. The resolution affirms that religious freedom includes the right of individuals of any faith and individuals of no faith to live, work, associate, and worship in accordance with their beliefs; all people of the United States can be unified in supporting religious freedom because it is a fundamental human right; and the American people will remain forever unshackled in matters of faith.'}

In [12]:
generated_summaries[3]

{'generated': '2023-02-16 Introduced in Senate This concurrent resolution requires the Joint Committee on the Library to approve or deny the statue of Rev. Billy Graham . this file contains bill summaries for federal legislation and details the effects the legislative text may have on current law and federal programs .',
 'summary': 'This concurrent resolution requires the Joint Committee on the Library to approve or deny the statue of Rev. Billy Graham for placement in the National Statuary Hall within 30 days after North Carolina submits specific information about the statute, including its dimensions and final weight.'}

In [13]:
generated_summaries[4]

{'generated': '2023-03-09 Introduced in Senate This concurrent resolution declares that Congress should not impose any new performance fee, tax, royalty, or other charge relating to the public performance of sound recordings on a local radio station . this file contains bill summaries for federal legislation .',
 'summary': 'This concurrent resolution declares that Congress should not impose any new performance fee, tax, royalty, or other charge relating to the public performance of sound recordings on a local radio station for broadcasting sound recordings over the air or on any business for such public performance of sound recordings.'}

In [14]:
generated_summaries[5]

{'generated': '2023-03-09 Introduced in Senate This concurrent resolution recognizes "Abortion Provider Appreciation Day" this file contains bill summaries for federal legislation . a bill summary describes the most significant provisions of a piece of legislation and details the effects the legislative text may have on current law .',
 'summary': 'This concurrent resolution recognizes Abortion Provider Appreciation Day.'}

In [15]:
generated_summaries[6]

{'generated': "2023-11-02 Passed Senate This concurrent resolution condemns Russia's unjust and arbitrary detention of Russian democratic opposition leader Vladimir Kara-Murza . it calls for his immediate release and the release of all other Russian opposition leaders .",
 'summary': "This concurrent resolution condemns Russia's unjust and arbitrary detention of Russian democratic opposition leader Vladimir Kara-Murza and calls for his immediate release and the release of all other Russian opposition leaders. It also calls for the release of all political prisoners in Russia and in Belarus, as well as for the release of Ukrainian citizens held by Russia, and calls on the President and leaders of the free world to work tirelessly for the release of political prisoners in Russia."}

In [16]:
generated_summaries[7]

{'generated': '2023-03-23 Introduced in Senate This concurrent resolution expresses the sense of Congress that tax-exempt fraternal benefit societies provide critical benefits to the people and communities of the united states . this file contains bill summaries for federal legislation and details the effects the legislative text may have on current law and federal programs .',
 'summary': 'This concurrent resolution expresses the sense of Congress that tax-exempt fraternal benefit societies provide critical benefits to the people and communities of the United States and their work should continue to be promoted.'}

In [17]:
generated_summaries[8]

{'generated': '2023-04-27 Introduced in Senate This concurrent resolution expresses the sense of Congress that climate change caused by human activities constitutes a climate emergency . it demands the president use existing authorities and emergency powers to mitigate and address its consequences and causes .',
 'summary': 'This concurrent resolution expresses the sense of Congress that climate change caused by human activities constitutes a climate emergency, which demands the President use existing authorities and emergency powers to mitigate and prepare for the consequences of the emergency.'}

In [18]:
generated_summaries[9]

{'generated': 'a bill summary describes the most significant provisions of a piece of legislation . the document is not subject to copyright protection and is in the public domain . it is authored by the Congressional Research Service .',
 'summary': "Fiscal State of the Nation Resolution This concurrent resolution requires the congressional budget committees to conduct an annual joint hearing to receive a presentation from the Comptroller General regarding (1) the Government Accountability Office's audit of the financial statement of the executive branch, and (2) the financial position and condition of the federal government."}

In [19]:
generated_summaries[10]

{'generated': '2023-05-31 Introduced in Senate This concurrent resolution expresses the sense that the Senate should provide its advice and consent to ratification of the Convention on Biological Diversity . this file contains bill summaries for federal legislation and details the effects the legislative text may have on current law and federal programs .',
 'summary': 'This concurrent resolution expresses the sense that the Senate should provide its advice and consent to ratification of the Convention on Biological Diversity.'}

In [20]:
generated_summaries[11]

{'generated': '2023-07-18 Introduced in Senate This concurrent resolution calls on the media to voluntarily adopt certain practices . it calls for coverage that (1) denies murderers a public platform; (2) minimizes the potential for media reporting to increase the likelihood of future mass public murders .',
 'summary': 'This concurrent resolution calls on the media to voluntarily adopt certain practices to prevent further harm from its coverage of mass public murders. Specifically, it calls for coverage that (1) denies murderers a public platform; (2) minimizes the potential for media reporting to increase the likelihood of future mass public murders (i.e., the media contagion effect); and (3) prioritizes the victims of, and heroism in the response to, mass public murders.'}

In [21]:
generated_summaries[12]

{'generated': '2023-07-27 Introduced in Senate This concurrent resolution affirms, more than 400 years after the arrival of the first slave ship, that the United States owes a debt of remembrance to those who lived through slavery . it urges the establishment of a U.S. Commission on Truth, Racial Healing, and Transformation .',
 'summary': 'This concurrent resolution affirms, more than 400 years after the arrival of the first slave ship, that the United States owes a debt of remembrance to those who lived through slavery or other historical injustices against people of color, as well as to their descendants. It also urges the establishment of a U.S. Commission on Truth, Racial Healing, and Transformation.'}

In [22]:
generated_summaries[13]

{'generated': '2023-10-04 Introduced in Senate This concurrent resolution recognizes the disparity between wages paid to Latina women in comparison to men . a bill summary describes the most significant provisions of a piece of legislation .',
 'summary': "This concurrent resolution recognizes the disparity between wages paid to Latina women in comparison to men and reaffirms Congress's support for ensuring equal pay and closing the gender wage gap."}

In [23]:
generated_summaries[14]

{'generated': '2023-10-26 Introduced in Senate This concurrent resolution expresses the sense of Congress that a carbon tax would be detrimental to families and businesses . this file contains bill summaries for federal legislation and details the effects the legislative text may have on current law and federal programs .',
 'summary': 'This concurrent resolution expresses the sense of Congress that a carbon tax would be detrimental to families and businesses and would severely harm the economic and national security of the country.'}

In [24]:
generated_summaries[15]

{'generated': '2024-02-13 Introduced in Senate This concurrent resolution provides for a correction in the official title of H.R. 815 . a bill summary describes the most significant provisions of a piece of legislation .',
 'summary': 'This concurrent resolution makes a correction to the official title of H.R. 815 (Making emergency supplemental appropriations for the fiscal year ending September 30, 2024, and for other purposes).'}

# ROUGE EVALUATION

In [1]:
import evaluate

rouge = evaluate.load("rouge")

def ROUGE_evaluate(data_set : list):
    date = data_set
    for i in range(len(generated_summaries)):
        rouge = evaluate.load('rouge')
        predictions = [generated_summaries[i]['generated']]
        references = [generated_summaries[i]['summary']]
        results = rouge.compute(predictions=predictions, references=references)
        print(results)

2024-04-12 23:41:17.816687: I tensorflow/core/util/port.cc:111] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-04-12 23:41:17.854792: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-04-12 23:41:17.854821: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-04-12 23:41:17.854843: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-04-12 23:41:17.861609: I tensorflow/core/platform/cpu_feature_g

In [27]:
ROUGE_evaluate(generated_summaries)

{'rouge1': 0.7538461538461538, 'rouge2': 0.71875, 'rougeL': 0.7230769230769232, 'rougeLsum': 0.7230769230769232}
{'rouge1': 0.5325443786982248, 'rouge2': 0.4790419161676647, 'rougeL': 0.5207100591715977, 'rougeLsum': 0.5207100591715977}
{'rouge1': 0.7338129496402878, 'rouge2': 0.7153284671532847, 'rougeL': 0.7194244604316548, 'rougeLsum': 0.7194244604316548}
{'rouge1': 0.5319148936170212, 'rouge2': 0.41304347826086957, 'rougeL': 0.5106382978723404, 'rougeLsum': 0.5106382978723404}
{'rouge1': 0.6808510638297872, 'rouge2': 0.6521739130434783, 'rougeL': 0.6808510638297872, 'rougeLsum': 0.6808510638297872}
{'rouge1': 0.2909090909090909, 'rouge2': 0.2641509433962264, 'rougeL': 0.2909090909090909, 'rougeLsum': 0.2909090909090909}
{'rouge1': 0.5499999999999999, 'rouge2': 0.5084745762711864, 'rougeL': 0.5333333333333333, 'rougeLsum': 0.5333333333333333}
{'rouge1': 0.6067415730337079, 'rouge2': 0.5747126436781609, 'rougeL': 0.6067415730337079, 'rougeLsum': 0.6067415730337079}
{'rouge1': 0.78048